This notebook provide tools to evaluate your trained models qualitatively. You can:

* Create a pianoroll viz (from a NoteSequence with BokehJS).
* Synthesize & download audio (from a NoteSequence with the gorgeous Yamaha C5 Salamander SoundFont).

* ~Run inference on unseen data~ <-- No


--- 

## Environment Setup

**JUPYTER**
* Do not use Jupyter Lab. It disables JS which breaks Bokeh and the pianoroll.
* Start a regular Jupyter Notebook with ~increased~ data rate. Otherwise the audio synthesis overflows.
    * `jupyter notebook --NotebookApp.iopub_data_rate_limit=10000000 1.5\ Interactively\ Explore.ipynb`
    
**FILE DEPENDENCIES**
* Salamander piano SoundFont. Samples by Alexander Holm [[Link](https://archive.org/details/SalamanderGrandPianoV3)]. Converted to sf2 by John Nebauer [[Link](https://sites.google.com/site/soundfonts4u)]. You can fetch those from here (591.9 MiB):
    * `gsutil -m cp gs://download.magenta.tensorflow.org/soundfonts/Yamaha-C5-Salamander-JNv5.1.sf2 /tmp/`
    
**OTHER DEPENDENCIES**
To synthesize audio, you will need `fluidsynth` [[Homepage](http://www.fluidsynth.org/)] [[GitHub](https://github.com/FluidSynth/fluidsynth)] and `pyfluidsynth` [[GitHub](https://github.com/nwhitehead/pyfluidsynth)]. Be warned, those can be a pain to install. 
* `fluidsynth` failed repeatingly with `brew`. Eventually, installation worked with `macports` after I updated the entire tree (which took ages).
* `pyfluidsynth` implements Python bindings. Note that there are a few forks floating online. Some of the high ranking results on Google are dated version for Python 2.7. In the end, [this](https://github.com/nwhitehead/pyfluidsynth) worked for me.
* Keep in mind as well that there is a PyPI (`pip install`) module called `fluidsynth` which you must NOT installed.
    
    
    
Lastly, this Jupyter borrows backend from the [Magenta Performance RNN Colaboratory](https://colab.research.google.com/notebooks/magenta/performance_rnn/performance_rnn.ipynb?authuser=0#scrollTo=nzGyqJja7I0O).

# First Things First

In [21]:
import os
import sys
import inspect
from pathlib import Path
currentdir = os.path.dirname(os.path.abspath(inspect.getfile(inspect.currentframe())))
parentdir = Path(currentdir).parents[1]
sys.path.insert(0, os.path.join(parentdir, 'utils'))

In [26]:
from text_seqs import TextSequence, TextSequenceCollection

In [132]:
config = {}
config['steps_per_quarter'] = 4

config['inputs'] = '../../assets/data/processed/heron/eval_inputs.txt'
config['targets'] = '../../assets/data/processed/heron/eval_targets.txt'
config['predicted'] = '../../assets/trained_models/2018_07_05_0645/run_dir/model_dir/eval/predictions.txt.8000'

In [133]:
inputs = TextSequenceCollection(config['inputs'])
predicted = TextSequenceCollection(config['predicted'])
targets = TextSequenceCollection(config['targets'])

In [135]:
# predicted.as_note_seq[235].notes

# Interactive

In [136]:
i = 145 # is the worst
i = 18
# i = 36
# i = 32
i = 38
# i = 8

### Inputs

In [137]:
inputs.viz(i)
inputs.synth(i)

Loading BokehJS ...

### Predicted

In [140]:
predicted.viz(i)
predicted.synth(i)

Loading BokehJS ...

### Targets

In [141]:
targets.viz(i)
targets.synth(i)

Loading BokehJS ...

## Experiments

In [314]:
# score.show()

In [277]:
ts = music21.meter.bestTimeSignature(score)
print('Beat Division Count \t', ts.beatDivisionCount)
print('Beat Count \t\t', ts.beatCount)
print('Beat Division Name \t',  music21.meter.bestTimeSignature(score).beatDivisionCountName) # Simple or Compound
print('---')
print('Numerator \t', ts.numerator)
print('Denominator \t', ts.denominator)
print('---')
print(ts.beatDivisionDurations)
print(ts.beatDuration)


Beat 			 1.0
Beat Division Count 	 2
Beat Count 		 48
Beat Division Name 	 Simple
---
Numerator 	 48
Denominator 	 4
---
[<music21.duration.Duration 0.5>, <music21.duration.Duration 0.5>]
<music21.duration.Duration 1.0>


In [260]:
# ambitus: measures register, the range of pitches used in a melodic line
ambitus = score.analyze('ambitus')


# Compute the relative amount of each semitone across the entire song
# A proxy for key
print('Key Proxy \t', sum(sum(pretty_midi.get_chroma())))

Key Proxy 	 769100.0


In [39]:
# For a given subStream, return the smallest .ps difference between any two pitches 
# and the largest difference between any two pitches. This is used to get the smallest 
# and largest ambitus possible in a given work.
p = music21.analysis.discrete.Ambitus()
p.getPitchRanges(score)

(0, 17)

In [40]:
p.getPitchSpan(score)

(<music21.pitch.Pitch C4>, <music21.pitch.Pitch F5>)

In [ ]:
# score.show()